# Install Pacakges Needed

---



In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
!pip install tpot mljar-supervised

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 87 kB 3.3 MB/s 
     |████████████████████████████████| 112 kB 42.2 MB/s 
     |████████████████████████████████| 139 kB 43.0 MB/s 
     |████████████████████████████████| 255.9 MB 46 kB/s 
     |████████████████████████████████| 2.0 MB 41.0 MB/s 
     |████████████████████████████████| 76.6 MB 1.2 MB/s 
     |████████████████████████████████| 72 kB 725 kB/s 
     |████████████████████████████████| 569 kB 51.0 MB/s 
     |████████████████████████████████| 72 kB 751 kB/s 
     |████████████████████████████████| 348 kB 48.3 MB/s 
     |████████████████████████████████| 81 kB 9.4 MB/s 
     |████████████████████████████████| 209 kB 37.5 MB/s 
     |████████████████████████████████| 78 kB 7.0 MB/s 
     |████████████████████████████████| 147 kB 52.1 MB/s 
     |████████████████████████████████| 50 kB 6.3 MB/s 
     |████████████████████████████████| 112

In [33]:
import pandas as pd
from supervised.automl import AutoML
import os

from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split

import numpy as np
import supervised

import warnings

from sklearn import datasets
from sklearn.pipeline import make_pipeline
from sklearn.decomposition import PCA

from supervised.exceptions import AutoMLException

# Healthcare Dataset - SPARCS

## Load in dataset

In [3]:
import pandas as pd
sparcs = pd.read_csv('https://raw.githubusercontent.com/hantswilliams/HHA-507-2022/main/autoML/datasets/data_sparcs.csv')
sparcs

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Risk of Mortality APR Medical Surgical Description  \
0      ...                 Minor                          Medical   
1      ...                 Minor                          Medical   
2      ...                 Minor                          Medical   
3      ...              Moderate                          Medical   
4      ...                 Major                          Medical   
...    ...                   ...                              ...   
23578  ...              Moderate                          Medical   
23579  ...                 Minor                          Medical   
23580  ...                 Minor                          Medical   
23581  ...                 Major                          Medical   
23582  ...                 Major                          Medical   

             Payment Typology 1        Payment Typology 2  Payment Typology 3  \
0      Private Health Insurance                       NaN                 NaN   
1        Blue Cross/Blue Shield                  Self-Pay            Self-Pay   
2                      Self-Pay                  Self-Pay            Self-Pay   
3                      Medicare                  Medicare            Self-Pay   
4        Blue Cross/Blue Shield  

In [4]:
sparcs.columns

Index(['Health Service Area', 'Hospital County',
       'Operating Certificate Number', 'Facility Id', 'Facility Name',
       'Age Group', 'Zip Code - 3 digits', 'Gender', 'Race', 'Ethnicity',
       'Length of Stay', 'Type of Admission', 'Patient Disposition',
       'Discharge Year', 'CCS Diagnosis Code', 'CCS Diagnosis Description',
       'CCS Procedure Code', 'CCS Procedure Description', 'APR DRG Code',
       'APR DRG Description', 'APR MDC Code', 'APR MDC Description',
       'APR Severity of Illness Code', 'APR Severity of Illness Description',
       'APR Risk of Mortality', 'APR Medical Surgical Description',
       'Payment Typology 1', 'Payment Typology 2', 'Payment Typology 3',
       'Birth Weight', 'Abortion Edit Indicator',
       'Emergency Department Indicator', 'Total Charges', 'Total Costs'],
      dtype='object')

## Potential variables of interest

- Type of Admission (categorical) 
- Total Charges (continuous)

In [18]:
sparcs['Type of Admission'].value_counts()

Emergency        14968
Elective          4508
Newborn           2285
Urgent            1743
Trauma              63
Not Available       16
Name: Type of Admission, dtype: int64

In [7]:
sparcs['Total Charges'].describe()

count    2.358300e+04
mean     4.344052e+04
std      8.434949e+04
min      1.000000e+00
25%      1.226175e+04
50%      2.375403e+04
75%      4.702837e+04
max      4.410671e+06
Name: Total Charges, dtype: float64

# MLJar Examples

## Mutlti-Class Example 1 - SPARCS

### **Create new model**

In [19]:
X = sparcs.drop(columns=['Type of Admission'])

In [20]:
X.columns

Index(['Health Service Area', 'Hospital County',
       'Operating Certificate Number', 'Facility Id', 'Facility Name',
       'Age Group', 'Zip Code - 3 digits', 'Gender', 'Race', 'Ethnicity',
       'Patient Disposition', 'Discharge Year', 'CCS Diagnosis Code',
       'CCS Diagnosis Description', 'CCS Procedure Code',
       'CCS Procedure Description', 'APR DRG Code', 'APR DRG Description',
       'APR MDC Code', 'APR MDC Description', 'APR Severity of Illness Code',
       'APR Severity of Illness Description', 'APR Risk of Mortality',
       'APR Medical Surgical Description', 'Payment Typology 1',
       'Payment Typology 2', 'Payment Typology 3', 'Birth Weight',
       'Abortion Edit Indicator', 'Emergency Department Indicator',
       'Total Charges', 'Total Costs', 'sparcs_los'],
      dtype='object')

In [25]:
Y = sparcs['Type of Admission']

In [22]:
X

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Medical Surgical Description        Payment Typology 1  \
0      ...                          Medical  Private Health Insurance   
1      ...                          Medical    Blue Cross/Blue Shield   
2      ...                          Medical                  Self-Pay   
3      ...                          Medical                  Medicare   
4      ...                          Medical    Blue Cross/Blue Shield   
...    ...                              ...                       ...   
23578  ...                          Medical                  Medicare   
23579  ...                          Medical  Private Health Insurance   
23580  ...                          Medical                  Medicaid   
23581  ...                          Medical                  Medicare   
23582  ...                          Medical                  Medicare   

             Payment Typology 2 Payment Typology 3  Birth Weight  \
0                           NaN                NaN             0   
1                      Self-Pay           Self-Pay             0   
2                      Self-Pay           Self-Pay          2900   
3                      Medicare           Self-Pay             0   
4                      Medicare           Self-Pay

In [26]:
Y

0           Urgent
1           Urgent
2          Newborn
3        Emergency
4        Emergency
           ...    
23578    Emergency
23579      Newborn
23580       Urgent
23581    Emergency
23582    Emergency
Name: Type of Admission, Length: 23583, dtype: object

In [28]:
X_train, X_test, Y_train, Y_test = train_test_split(X, Y, stratify=Y, test_size=0.25)

In [29]:
automl = AutoML(
    results_path="sparcs_type_of_admission",
    mode="Explain"
)

In [30]:
automl.fit(X_train, Y_train)

Linear algorithm was disabled.
AutoML directory: sparcs_type_of_admission
The task is multiclass_classification with evaluation metric logloss
AutoML will use algorithms: ['Baseline', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 2 models
1_Baseline logloss 1.047051 trained in 0.77 seconds


2_DecisionTree logloss 0.378191 trained in 31.04 seconds
* Step default_algorithms will try to check up to 3 models
3_Default_Xgboost logloss 0.222508 trained in 66.6 seconds
4_Default_NeuralNetwork logloss 0.359378 trained in 7.68 seconds
5_Default_RandomForest logloss 0.344678 trained in 36.85 seconds
* Step ensemble will try to check up to 1 model
Ensemble logloss 0.222508 trained in 0.61 seconds
AutoML fit time: 154.36 seconds
AutoML best model: 3_Default_Xgboost


AutoML(results_path='sparcs_type_of_admission')

In [31]:
pred = automl.predict(X_test)
pred

array(['Newborn', 'Emergency', 'Emergency', ..., 'Elective', 'Elective',
       'Emergency'], dtype=object)

In [32]:
automl.report()

## Continuous - Example 2 - SPARCS

In [34]:
x_cols = [c for c in sparcs.columns if c != 'Total Charges']
x = sparcs[x_cols]
y = sparcs['Total Charges']

In [35]:
x_cols

['Health Service Area',
 'Hospital County',
 'Operating Certificate Number',
 'Facility Id',
 'Facility Name',
 'Age Group',
 'Zip Code - 3 digits',
 'Gender',
 'Race',
 'Ethnicity',
 'Type of Admission',
 'Patient Disposition',
 'Discharge Year',
 'CCS Diagnosis Code',
 'CCS Diagnosis Description',
 'CCS Procedure Code',
 'CCS Procedure Description',
 'APR DRG Code',
 'APR DRG Description',
 'APR MDC Code',
 'APR MDC Description',
 'APR Severity of Illness Code',
 'APR Severity of Illness Description',
 'APR Risk of Mortality',
 'APR Medical Surgical Description',
 'Payment Typology 1',
 'Payment Typology 2',
 'Payment Typology 3',
 'Birth Weight',
 'Abortion Edit Indicator',
 'Emergency Department Indicator',
 'Total Costs',
 'sparcs_los']

In [36]:
x

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Risk of Mortality APR Medical Surgical Description  \
0      ...                 Minor                          Medical   
1      ...                 Minor                          Medical   
2      ...                 Minor                          Medical   
3      ...              Moderate                          Medical   
4      ...                 Major                          Medical   
...    ...                   ...                              ...   
23578  ...              Moderate                          Medical   
23579  ...                 Minor                          Medical   
23580  ...                 Minor                          Medical   
23581  ...                 Major                          Medical   
23582  ...                 Major                          Medical   

             Payment Typology 1        Payment Typology 2 Payment Typology 3  \
0      Private Health Insurance                       NaN                NaN   
1        Blue Cross/Blue Shield                  Self-Pay           Self-Pay   
2                      Self-Pay                  Self-Pay           Self-Pay   
3                      Medicare                  Medicare           Self-Pay   
4        Blue Cross/Blue Shield       

In [37]:
y

0         4757.01
1         5090.25
2         4948.50
3         4719.75
4        50384.75
           ...   
23578    50833.00
23579    10948.00
23580    46421.00
23581    46122.00
23582    32225.00
Name: Total Charges, Length: 23583, dtype: float64

In [44]:
automl2 = AutoML(
      results_path="sparcs_total_charges",
      mode="Explain"
)

In [45]:
automl2.fit(x, y)

Linear algorithm was disabled.
AutoML directory: sparcs_total_charges
The task is regression with evaluation metric rmse
AutoML will use algorithms: ['Baseline', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 2 models
1_Baseline rmse 72381.653229 trained in 1.01 seconds
2_DecisionTree rmse 33806.950052 trained in 11.27 seconds
* Step default_algorithms will try to check up to 3 models
3_Default_Xgboost rmse 19317.244911 trained in 114.9 seconds
4_Default_NeuralNetwork rmse 41133.005568 trained in 5.52 seconds
5_Default_RandomForest rmse 35259.613876 trained in 23.41 seconds
* Step ensemble will try to check up to 1 model
Ensemble rmse 18321.0384 trained in 0.29 seconds
AutoML fit time: 165.07 seconds
AutoML best model: Ensemble


AutoML(results_path='sparcs_total_charges')

In [46]:
sparcs["predictions"] = automl2.predict(x)


In [47]:
print("Predictions")
print(sparcs[['Total Charges', 'predictions']].head())

Predictions
   Total Charges   predictions
0        4757.01   7549.839851
1        5090.25   7578.697663
2        4948.50   7467.789851
3        4719.75   7484.809382
4       50384.75  53494.907570


# Download outputs

In [48]:
# get current working directory
import os
os.getcwd()

'/content'

In [49]:
folders = os.listdir()
foldersML = [x for x in folders if x.startswith('sparcs')]
print(foldersML)

['sparcs_type_of_admission', 'sparcs_total_charges', 'sparcs_type_of_admission.zip']


In [43]:
!zip -r /content/sparcs_type_of_admission.zip /content/sparcs_type_of_admission

  adding: content/sparcs_type_of_admission/ (stored 0%)
  adding: content/sparcs_type_of_admission/data_info.json (deflated 84%)
  adding: content/sparcs_type_of_admission/ldb_performance_boxplot.png (deflated 22%)
  adding: content/sparcs_type_of_admission/4_Default_NeuralNetwork/ (stored 0%)
  adding: content/sparcs_type_of_admission/4_Default_NeuralNetwork/status.txt (stored 0%)
  adding: content/sparcs_type_of_admission/4_Default_NeuralNetwork/permutation_importance.png (deflated 15%)
  adding: content/sparcs_type_of_admission/4_Default_NeuralNetwork/learner_fold_0_importance.csv (deflated 46%)
  adding: content/sparcs_type_of_admission/4_Default_NeuralNetwork/README.md (deflated 73%)
  adding: content/sparcs_type_of_admission/4_Default_NeuralNetwork/confusion_matrix_normalized.png (deflated 11%)
  adding: content/sparcs_type_of_admission/4_Default_NeuralNetwork/confusion_matrix.png (deflated 12%)
  adding: content/sparcs_type_of_admission/4_Default_NeuralNetwork/precision_recall_c

In [50]:
!zip -r /content/sparcs_total_charges.zip /content/sparcs_total_charges

  adding: content/sparcs_total_charges/ (stored 0%)
  adding: content/sparcs_total_charges/data_info.json (deflated 84%)
  adding: content/sparcs_total_charges/ldb_performance_boxplot.png (deflated 22%)
  adding: content/sparcs_total_charges/4_Default_NeuralNetwork/ (stored 0%)
  adding: content/sparcs_total_charges/4_Default_NeuralNetwork/status.txt (stored 0%)
  adding: content/sparcs_total_charges/4_Default_NeuralNetwork/permutation_importance.png (deflated 15%)
  adding: content/sparcs_total_charges/4_Default_NeuralNetwork/learner_fold_0_importance.csv (deflated 46%)
  adding: content/sparcs_total_charges/4_Default_NeuralNetwork/true_vs_predicted.png (deflated 12%)
  adding: content/sparcs_total_charges/4_Default_NeuralNetwork/README.md (deflated 51%)
  adding: content/sparcs_total_charges/4_Default_NeuralNetwork/predicted_vs_residuals.png (deflated 14%)
  adding: content/sparcs_total_charges/4_Default_NeuralNetwork/learner_fold_0.neural_network (deflated 0%)
  adding: content/spar